# Compare the two raters

In [2]:
import pandas as pd
import numpy as np
from os.path import join as opj
from sklearn.metrics import cohen_kappa_score
from Bio import Entrez
import pymed as pm # for pubmed querying
import metapub # for converting between doi and pmid
import glob
import os
from scidownl.scihub import *
import metapub # for converting DOIs and pmids
import time
import random

2020-12-15 13:26:45 PinaColada-5.local metapub.config[10311] WARNING NCBI_API_KEY was not set.


In [3]:
# change width of notebook
from IPython.core.display import display, HTML
display(HTML("<style>.container { width:95% !important; }</style>"))

# change max row pandas will spit out
pd.set_option('display.max_rows', 5000)
pd.options.display.max_colwidth = 1000

In [4]:
if os.getcwd().split('/')[-1] == 'interference_in_the_subcortex':
    print('In the correct working directory: ' + str(os.getcwd()))
else:
    os.chdir("..")
    print('Changed to correct working directory: ' + str(os.getcwd()))

Changed to correct working directory: /Users/scotti/surfdrive/Projects/interference_in_the_subcortex


In [4]:
# set some directories
sheets_dir = opj(os.getcwd(), 'notebooks/rated_articles')

In [5]:
# load in rater 1 information
mck = pd.read_excel(opj(sheets_dir,'checked_articles_mck.xlsx'),index_col=0)
mck['pmid'] = mck['pmid'].astype(str)
mck.set_index('pmid',inplace=True)
mck = mck.rename(columns={'rater':'rater1'})

In [6]:
# load in rater 2 information
sct = pd.read_excel(opj(sheets_dir,'checked_articles_sct.xlsx'),index_col=0)
sct['pmid'] = sct['pmid'].astype(str)
sct.set_index('pmid',inplace=True)
sct = sct.reindex(mck.index) # reindex so they are the same order
sct = sct.rename(columns={'rater':'rater2'})

In [7]:
# Print some descriptive checks before calculating inter rater reliability (IRR)
print('Rater 1 overall stats:')
print('no. ones = ' + str(len(mck.loc[mck['rater1']==1])))
print('no. twos = ' + str(len(mck.loc[mck['rater1']==2])))
print('no. threes = ' + str(len(mck.loc[mck['rater1']==3])))
print('no. fours = ' + str(len(mck.loc[mck['rater1']==4])))
print('no. misses = ' + str(len(mck.loc[mck['rater1']=='-'])))

print('')

print('Rater 2 overall stats:')
print('no. ones = ' + str(len(sct.loc[sct['rater2']==1])))
print('no. twos = ' + str(len(sct.loc[sct['rater2']==2])))
print('no. threes = ' + str(len(sct.loc[sct['rater2']==3])))
print('no. fours = ' + str(len(sct.loc[sct['rater2']==4])))
print('no. misses = ' + str(len(sct.loc[sct['rater2']=='-'])))

Rater 1 overall stats:
no. ones = 535
no. twos = 121
no. threes = 18894
no. fours = 46
no. misses = 2

Rater 2 overall stats:
no. ones = 636
no. twos = 318
no. threes = 18598
no. fours = 45
no. misses = 0


/Users/scotti/anaconda3/lib/python3.7/site-packages/pandas/core/ops.py:1649: FutureWarning: elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison
  result = method(y)


In [8]:
# Replace two of rater 1's missed with '3' as they are not on the topic of this meta-analysis
mck.loc[mck.rater1=='-'] = 3
# Replace one of rater 2's ratings with '3' as they accidently put '33'
sct.loc[sct.rater2==33] = 3

In [9]:
IRR = cohen_kappa_score(list(mck['rater1']),list(sct['rater2']))
IRR # IRR is ok

0.6901174585847898

# Check how many full texts we are going to need to download

- all papers where we both stated '1' -> download the full text
- all papers where either of us stated '1' and the other stated '2' -> download the full text
- all papers where both of us stated '2' -> download the full text
- all paper where either of us stated '1' or '2' and the other stated '3' -> we need to discuss 
- all papers where either of us stated '4' -> download the review and place it in a folder for cross referencing
- all papers where both of us stated '3' -> discard

In [10]:
# Move data frames around
compframe = pd.concat([mck,sct['rater2']],axis=1)
print(len(compframe))
#compframe.head(3)

19598


In [11]:
# Papers to download full texts that:
# 1) Are both rated as 1
# 2) Where one is rated as 2 and one as 1
# 3) where both are rated as 2
full_texts = compframe.loc[(((compframe.rater1==1) & (compframe.rater2==1)) | 
                           ((compframe.rater1==1) & (compframe.rater2==2)) |
                           ((compframe.rater1==2) & (compframe.rater2==1)) |
                           ((compframe.rater1==2) & (compframe.rater2==2))),]
print('Articles to download full texts of: ' + str(len(full_texts)))
#full_texts.head(3)

Articles to download full texts of: 591


In [12]:
# Papers to discuss because:
# One rated as (1 or 2) and one rated as 3
to_discuss = compframe.loc[(((compframe.rater1==1) & (compframe.rater2==3)) | 
                           ((compframe.rater1==2) & (compframe.rater2==3)) |
                           ((compframe.rater1==3) & (compframe.rater2==1)) |
                           ((compframe.rater1==3) & (compframe.rater2==2))),]
print('Articles to discuss: ' + str(len(to_discuss)))
#to_discuss.head(3)

Articles to discuss: 425


In [13]:
# Papers to discard: 
# 1) as both raters rated as 3
to_discard = compframe.loc[((compframe.rater1==3) & (compframe.rater2==3)),]
print('Articles to discard: ' + str(len(to_discard)))
#to_discard.head(3)

Articles to discard: 18526


In [14]:
# Papers rated as reviews (4)
reviews = compframe.loc[((compframe.rater1==4) | (compframe.rater2==4)),]
print("Number of reviews found: " + str(len(reviews)))
#reviews.head(3)

Number of reviews found: 56


In [15]:
# Print info and recheck no papers were left out
s = f"""
Articles to download full texts of: {len(full_texts)}
Articles to discuss: {len(to_discuss)}
Articles to discard: {len(to_discard)}
Number of reviews found: {len(reviews)}
Number of articles here ({len(full_texts)+len(to_discuss)+len(to_discard)+len(reviews)}) should equal total number of articles ({len(compframe)})
"""
print(s)


Articles to download full texts of: 591
Articles to discuss: 425
Articles to discard: 18526
Number of reviews found: 56
Number of articles here (19598) should equal total number of articles (19598)



# Re-review 425 abstracts that were not agreed on.

In [16]:
mck_discuss = to_discuss.iloc[:,0:6]
mck_discuss['rater1'] = '-'
sct_discuss = mck_discuss
sct_discuss = sct_discuss.rename(columns={'rater1':'rater2'})

mck_discuss = mck_discuss.sample(frac=1)#.reset_index(drop=True)
sct_discuss = sct_discuss.sample(frac=1)

In [17]:
tocheck_dir = opj(os.getcwd(), 'notebooks/to_recheck_articles')

# already ran code below. Don't run again
#sct_discuss.to_excel(opj(tocheck_dir, 'recheck_articles_sct.xlsx'), sheet_name = 'pmid_sct')
#mck_discuss.to_excel(opj(tocheck_dir, 'recheck_articles_mck.xlsx'), sheet_name = 'pmid_mck')

## Go through rechecked articles and divide based on the above criteria

In [18]:
# set some directories
recheck_dir = opj(os.getcwd(), 'notebooks/rechecked_articles')

In [19]:
# load in rater information
mck_re = pd.read_excel(opj(recheck_dir,'rechecked_articles_mck.xlsx'),index_col=0)
sct_re = pd.read_excel(opj(recheck_dir,'rechecked_articles_sct.xlsx'),index_col=0)
sct_re = sct_re.reindex(mck_re.index) # reindex so they are the same order

In [20]:
# Print some descriptive checks before calculating inter rater reliability (IRR)
print('Rater 1 overall stats:')
print('no. ones = ' + str(len(mck_re.loc[mck_re['rater1']==1])))
print('no. twos = ' + str(len(mck_re.loc[mck_re['rater1']==2])))
print('no. threes = ' + str(len(mck_re.loc[mck_re['rater1']==3])))
print('no. misses = ' + str(len(mck_re.loc[mck_re['rater1']=='-'])))

print('')

print('Rater 2 overall stats:')
print('no. ones = ' + str(len(sct_re.loc[sct_re['rater2']==1])))
print('no. twos = ' + str(len(sct_re.loc[sct_re['rater2']==2])))
print('no. threes = ' + str(len(sct_re.loc[sct_re['rater2']==3])))
print('no. misses = ' + str(len(sct_re.loc[sct_re['rater2']=='-'])))

Rater 1 overall stats:
no. ones = 149
no. twos = 23
no. threes = 253
no. misses = 0

Rater 2 overall stats:
no. ones = 134
no. twos = 24
no. threes = 267
no. misses = 0


In [21]:
IRR_re = cohen_kappa_score(list(mck_re['rater1']),list(sct_re['rater2']))
IRR_re # IRR_re is ok

0.7153074895198582

## Inter rater agreement is OK, split articles like above

- all papers where we both stated '1' -> download the full text
- all papers where either of us stated '1' and the other stated '2' -> download the full text
- all papers where both of us stated '2' -> download the full text
- all paper where either of us stated '1' or '2' and the other stated '3' -> we need to discuss 
- all papers where either of us stated '4' -> download the review and place it in a folder for cross referencing
- all papers where both of us stated '3' -> discard

In [22]:
# Move data frames around
compframe_re = pd.concat([mck_re,sct_re['rater2']],axis=1)
print(len(compframe_re))
#compframe_re.head(3)

425


In [23]:
# Papers to download full texts that:
# 1) Are both rated as 1
# 2) Where one is rated as 2 and one as 1
# 3) where both are rated as 2
full_texts = full_texts.append(compframe_re.loc[(((compframe_re.rater1==1) & (compframe_re.rater2==1)) | 
                           ((compframe_re.rater1==1) & (compframe_re.rater2==2)) |
                           ((compframe_re.rater1==2) & (compframe_re.rater2==1)) |
                           ((compframe_re.rater1==2) & (compframe_re.rater2==2))),])
print('Articles to download full texts of: ' + str(len(full_texts)))
#full_texts.head(3)

Articles to download full texts of: 734


In [24]:
# Papers to discuss because:
# One rated as (1 or 2) and one rated as 3
to_discuss = compframe_re.loc[(((compframe_re.rater1==1) & (compframe_re.rater2==3)) | 
                           ((compframe_re.rater1==2) & (compframe_re.rater2==3)) |
                           ((compframe_re.rater1==3) & (compframe_re.rater2==1)) |
                           ((compframe_re.rater1==3) & (compframe_re.rater2==2))),]
print('Articles to discuss: ' + str(len(to_discuss)))
#to_discuss.head(3)

Articles to discuss: 44


In [25]:
# Papers to discard: 
# 1) as both raters rated as 3
to_discard = to_discard.append(compframe_re.loc[((compframe_re.rater1==3) & (compframe_re.rater2==3)),])
print('Articles to discard: ' + str(len(to_discard)))
#to_discard.head(3)

Articles to discard: 18764


In [26]:
# Print info and recheck no papers were left out
s = f"""
Numbers after re-review of 425 abstracts:
Articles to download full texts of: {len(full_texts)}
Articles to discuss: {len(to_discuss)}
Articles to discard: {len(to_discard)}
Number of reviews found: {len(reviews)}
Number of articles here ({len(full_texts)+len(to_discuss)+len(to_discard)+len(reviews)}) should equal total number of articles ({len(compframe)})
"""
print(s)


Numbers after re-review of 425 abstracts:
Articles to download full texts of: 734
Articles to discuss: 44
Articles to discard: 18764
Number of reviews found: 56
Number of articles here (19598) should equal total number of articles (19598)



## Output the 44 non-agreed articles to a table to go through again verbally

In [27]:
# save thse dataframe for both raters
save_dir = opj(os.getcwd(), 'notebooks/last_abstract_to_check')
new_to_discuss = to_discuss
new_to_discuss['final_rating'] = '-'
#new_to_discuss.to_excel(opj(save_dir, 'articles_to_discuss.xlsx'), sheet_name = 'pmid') # already ran this, don't run again

/Users/scotti/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  after removing the cwd from sys.path.


In [28]:
# load in verbally checked and agreed upon articles to finish the initial list 19598 abstracts
last_dir = opj(os.getcwd(), 'notebooks/last_abstract_to_check')
last_check = pd.read_excel(opj(last_dir,'discussed_articles.xlsx'),index_col=0)

In [29]:
# Papers to add to full texts that:
# 1) Are rated as 1
# 2) are rated as 2
full_texts = full_texts.append(last_check.ix[((last_check.final_rating==1) | (last_check.final_rating==2)),0:8]) 
print('Articles to download full texts of: ' + str(len(full_texts)))
#full_texts.head(3)

Articles to download full texts of: 755


/Users/scotti/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:4: DeprecationWarning: 
.ix is deprecated. Please use
.loc for label based indexing or
.iloc for positional indexing

See the documentation here:
http://pandas.pydata.org/pandas-docs/stable/indexing.html#ix-indexer-is-deprecated
  after removing the cwd from sys.path.


In [30]:
# Papers to discard: 
# 1) if final_rating is 3
to_discard = to_discard.append(last_check.ix[last_check.final_rating==3,0:8])
print('Articles to discard: ' + str(len(to_discard)))
#to_discard.head(3)

Articles to discard: 18787


/Users/scotti/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:3: DeprecationWarning: 
.ix is deprecated. Please use
.loc for label based indexing or
.iloc for positional indexing

See the documentation here:
http://pandas.pydata.org/pandas-docs/stable/indexing.html#ix-indexer-is-deprecated
  This is separate from the ipykernel package so we can avoid doing imports until


In [31]:
# No more artices to discuss
to_discuss = 0

In [32]:
# Print info and recheck no papers were left out
s = f"""
Numbers after verbal re-review of 44 abstracts:
Articles to download full texts of: {len(full_texts)}
Articles to discuss: {to_discuss}
Articles to discard: {len(to_discard)}
Number of reviews found: {len(reviews)}
Number of articles here ({len(full_texts)+to_discuss+len(to_discard)+len(reviews)}) should equal total number of articles ({len(compframe)})
"""
print(s)


Numbers after verbal re-review of 44 abstracts:
Articles to download full texts of: 755
Articles to discuss: 0
Articles to discard: 18787
Number of reviews found: 56
Number of articles here (19598) should equal total number of articles (19598)



## Now, download fulll text PDFs of the 56 meta-analyses we want to cross-reference with

In [33]:
# Download full texts of other meta-analyses on similar topics
# create empty dataframe to append to
DOIframe_metas = pd.DataFrame({'pmids': reviews.index, 'DOIs':'-'})

# loop over pmids to convert to DOIs
for pmid in DOIframe_metas.pmids:
    try:
        DOIframe_metas.loc[DOIframe_metas.pmids==pmid,'DOIs'] = metapub.convert.pmid2doi(pmid)
    except:
        print(DOIframe_metas.loc[DOIframe_metas.pmids==pmid])
        continue

In [34]:
# Now download full texts via sci hub for the reviews
from scidownl.scihub import *

# What folder to save in?
review_dir = '/Users/scotti/surfdrive/Projects/interference_in_the_subcortex/save_pdfs/reviews' 

# loop over DOIs from dataframe
for doi in DOIframe_metas.DOIs: 
    # save pdfs
    print(doi)
    # SciHub(doi, review_dir).download(choose_scihub_url_index=3) # already done don't do again

10.1016/j.neubiorev.2014.11.003
10.1016/j.tics.2018.10.007
10.3389/fnhum.2017.00154
10.1016/bs.pbr.2015.07.007
10.1016/j.neubiorev.2018.04.016
10.1017/S0033291720000574
10.1002/wcs.1471
10.1016/j.neuroimage.2015.03.053
10.1523/JNEUROSCI.3048-14.2014
10.1111/psyp.13032
10.1503/jpn.130052
10.1016/j.cobeha.2016.12.006
10.3389/fnhum.2012.00052
10.1016/j.jpsychires.2013.08.015
10.1016/j.tins.2019.07.004
10.1007/s00429-018-1727-9
10.1002/agm2.12037
10.1155/2013/820956
10.1016/j.jpsychires.2016.08.001
10.1007/s12311-011-0260-7
10.1017/S0033291713001037
10.1016/j.biopsych.2018.11.010
10.1016/j.bbr.2017.10.010
10.3389/fnhum.2014.00698
10.3758/s13423-018-1502-1
10.1016/j.neuropsychologia.2017.11.033
10.1016/j.jaac.2018.03.011
10.1016/j.pneurobio.2013.06.005
10.1016/j.neubiorev.2017.04.025
10.1186/s12993-018-0140-0
10.1016/j.neuroimage.2018.02.023
10.1523/JNEUROSCI.2348-16.2016
10.3389/fnbeh.2016.00220
10.1176/appi.ajp.2017.16040400
10.1037/neu0000200
10.1016/j.neubiorev.2018.04.022
10.1016/j.cpr

## Now, cross reference by the reference list of other meta-analyses

- each take 26 meta's, 
- create a list of DOI's,
- combine rater 1's with rater 2's, 
- check the overlap with initial pubmed query
- extract the abstracts of the new DOI's with python,
- each check the abstracts for inclusion

- get all pubmed id's of all articles cited or all articles used for the analysis part if available
- select only the ones that are published after 1 jan 2010
- exclude all pubmed id's that we've both agreed on not to include for full text in our initial query
- of the remaining pubmeds, exclude the ones that we've listed as reviews / meta analysis (label 4)
- of the remaining pubmeds, exclude the ones that we've already selected for full text inclusion
- that should leave only new pubmed id's

### First split the reviews between raters

In [35]:
# list all of the reviews to manually check
all_revs = glob.glob(opj(os.getcwd(), 'save_pdfs/reviews/*'))

# Give half of all reviews to rater 1
all_revs_mck = all_revs[:(len(all_revs)//2)]
# move to new folder
for i in all_revs_mck:
    old_loc = i.split('/')
    old_loc[-2] = 'revs_mck'
    new_loc = '/'.join(old_loc)
    #os.rename(i,new_loc)

# give other half of reviews to rater 2
all_revs_sct = all_revs[(len(all_revs)//2):]
# move to new folder
for i in all_revs_sct:
    old_loc = i.split('/')
    old_loc[-2] = 'revs_sct'
    new_loc = '/'.join(old_loc)
    #os.rename(i,new_loc)

# ABOVE CODE HAS ALREADY BEEN RUN

In [36]:
# Then print the length to make sure number was halved:
print(f'rater 1 has {len(glob.glob(opj(os.getcwd(), "save_pdfs/revs_mck/*")))} reviews to check')
print(f'rater 2 has {len(glob.glob(opj(os.getcwd(), "save_pdfs/revs_sct/*")))} reviews to check')

rater 1 has 28 reviews to check
rater 2 has 28 reviews to check


### Then combine and compare with inital pubmed query results

In [37]:
# load in pmids of new abstracts to check through
extra_doi_dir = opj(os.getcwd(), 'notebooks/dois_from_metas')
dois_to_add_sct = pd.read_excel(opj(extra_doi_dir,'doi_prev_metas_sct.xlsx'),index_col=0,keep_default_na=False)
dois_to_add_mck = pd.read_excel(opj(extra_doi_dir,'doi_prev_metas_mck.xlsx'),index_col=0,keep_default_na=False)
dois_to_add_mck.loc[dois_to_add_mck['pmid']=='NA','pmid'] = 'pre2010'

In [38]:
# Concatenate from both raters
dois_to_add_mck.columns = ['Meta','study','pmid','Note']
prev_meta_pmids = pd.concat([dois_to_add_sct[['Meta','study','pmid']],dois_to_add_mck[['Meta','study','pmid']]]).reset_index()

In [39]:
# calculate amount of potential previous literature
# There are 3189 previous articles
all_prev = len(prev_meta_pmids)
print(all_prev)

3189


In [40]:
# Now get rid of articles that:
# 1) Are from before 2010
# 2) do not have a pmid
# 3) Could not be found 
to_count_pre2010 = prev_meta_pmids.loc[prev_meta_pmids.pmid.isin(['pre2010'])]
counted_pre2010 = len(to_count_pre2010)

prev_pmids_to_check_dupe = prev_meta_pmids.loc[~prev_meta_pmids.pmid.isin(['pre2010','man','','-',' '])]
n_to_check =len(prev_pmids_to_check_dupe)
n_to_check

prev_pmids_to_check = prev_pmids_to_check_dupe.drop_duplicates(subset = "pmid", keep = 'first')
n_to_check_no_dupes = len(prev_pmids_to_check)

In [41]:
print(f"""
There were {all_prev} articles found from all previous meta-analyses
At least {counted_pre2010} of them were from before 2010 and not of interest
There were {n_to_check} to check with potential duplicates
After removing duplicates there are {n_to_check_no_dupes} to check
""")


There were 3189 articles found from all previous meta-analyses
At least 1091 of them were from before 2010 and not of interest
There were 2080 to check with potential duplicates
After removing duplicates there are 1649 to check



In [77]:
# # Use pmids from prev metas to get more articles to read abstracts of
# save_dir = opj(os.getcwd(), 'notebooks', 'to_check_prev_articles')

# pubmed = pm.PubMed(tool="MyTool", email = 'scott@leeclan.net')

# # pubmed = pm.PubMed(tool="MyTool", email = email) # this is already done above

# duplicate_checker = [] # setup list incase multiple articles are found (should only find one per PMID)

# article_info = pd.DataFrame(columns = ["title","authors","pmid","keywords","pubdate","abstract"]) # create pd object to append to

# counter = 1

# print(f'There are {len(prev_pmids_to_check)} articles to extract')

# for pmid_args in prev_pmids_to_check.pmid: # loop over all keyword argmuents
    
#     results = pubmed.query(query=pmid_args, max_results=2) # run search query
#     lengthable = pubmed.query(query=pmid_args, max_results=2) # non-elegant method to measure length of results
    
#     len_of_results = sum(1 for x in lengthable) # only way to get length of results output
    
#     if len_of_results > 1: # skip this PMID query search if more than one article comes up
#         duplicate_checker = duplicate_checker.append(pmid_args)
#         continue
#     elif len_of_results == 0:
#         print(f"PMID: {pmid_args} not found")
        
#     for article in results: # loop over all found articles
    
#         if '\n' in article.pubmed_id: # extract pubmed ID
#             article_id = article.pubmed_id.split('\n')[0]
#         else:
#             article_id = article.pubmed_id # extract info from each article
            
#         article_title = article.title # extract title

#         if hasattr(article,'keywords'):
#             if article.keywords: # find keywords if they exist
#                 if None in article.keywords:
#                     article.keywords.remove(None)
#                 article_keywords = '", "'.join(article.keywords)
#             else:
#                 article_keywords = "Article has no keywords"
            
#         article_publication_date = article.publication_date # extract publication date
#         article_abstract = article.abstract # extract abstract

#         article_authors = []
#         for auths in range(len(article.authors)):
#             if auths == len(article.authors)-1:
#                 if article.authors[auths]['lastname']==None or article.authors[auths]['firstname']==None:
#                     print('Skipping author, nonetype')
#                 else:
#                     article_authors.append(article.authors[auths]['lastname'] + ', ' + article.authors[auths]['initials'])
#             else:
#                 if article.authors[auths]['lastname']==None or article.authors[auths]['firstname']==None:
#                     print('Skipping author, nonetype')
#                 else:
#                     article_authors.append(article.authors[auths]['lastname'] + ', ' + article.authors[auths]['initials'] + '.,')
        
#         # Throw all this info into a pandas dataframe so we can export it to excel
#         article_info = article_info.append(pd.DataFrame({"title":[article_title],"authors":[str(' '.join(article_authors))],"pmid":[article_id],
#                                           "keywords":[article_keywords],"pubdate":[article_publication_date],
#                                           "abstract":[article_abstract]}))
        
#         # provide some output so we know what stage the code is at
#         if counter%50==0:
#             print(f'Processing article {counter}...')
#         counter += 1
        
#         time.sleep(0.5)
        
# # SAVE EXCEL DOCUMENT # already run, don't run again
# article_info.to_excel(opj(save_dir, 'prev_meta_abstracts.xlsx'), sheet_name = 'pmid_metas')

# print('Finished')

There are 1649 articles to extract
Processing article 50...
Processing article 100...
Skipping author, nonetype
Processing article 150...
Skipping author, nonetype
Processing article 200...
Processing article 250...
Processing article 300...
Processing article 350...
Processing article 400...
Processing article 450...
Processing article 500...
Processing article 550...
Skipping author, nonetype
Skipping author, nonetype
Skipping author, nonetype
Processing article 600...
Processing article 650...
Processing article 700...
Skipping author, nonetype
Skipping author, nonetype
Processing article 750...
Skipping author, nonetype
Skipping author, nonetype
Processing article 800...
Processing article 850...
Skipping author, nonetype
Processing article 900...
Processing article 950...
Skipping author, nonetype
Processing article 1000...
Processing article 1050...
Skipping author, nonetype
Processing article 1100...
Processing article 1150...
Processing article 1200...
Skipping author, nonetype

In [66]:
# SAVE EXCEL DOCUMENT
#article_info.to_excel(opj(os.getcwd(), 'notebooks', 'to_check_prev_articles', 'prev_meta_abstracts.xlsx'), , sheet_name = 'pmid_metas')

# LOAD DATA IN INSTEAD AS THE CODE HAS ALREADY BEEN RUN
article_info = pd.read_excel(opj(os.getcwd(), 'notebooks', 'to_check_prev_articles', 'prev_meta_abstracts.xlsx'), index_col=0)
article_info["pmid"] = article_info["pmid"].astype(str)

In [67]:
# check ns query serach ran correctly 
print(f'Length of article_info ({len(article_info)}) should be the same as n_to_check_no_dupes ({n_to_check_no_dupes})')

Length of article_info (1649) should be the same as n_to_check_no_dupes (1649)


In [68]:
# remove articles prior to 2010
article_info["pubdate"] = article_info["pubdate"].astype(str)
article_info = article_info[article_info['pubdate'].str.startswith(('2020','2019','2018','2017','2016','2015','2014','2013','2012','2011','2010'),na=False)]

In [69]:
after2010_prev = len(article_info)
after2010_prev
# there are 775 articles after or during 2010

987

In [70]:
# remove duplicates
article_info.drop_duplicates(subset = "pmid", keep = 'first', inplace = True)
article_info.reset_index(drop=True, inplace=True)
fin_prev = len(article_info)
fin_prev

908

In [71]:
# Now compare to the 19598 articles we already read the abstracts of to make sure we only look at new ones.
# compframe contains all of the pmids from the previuos abstract reviews
overlap = list(set(list(compframe.index)) & set(list(article_info.pmid)))
n_overlap = len(overlap)
print(f'There are {n_overlap} articles we have already looked at')

new_article_info = article_info.loc[~article_info.pmid.isin(overlap)].reset_index(drop=True)
n_new = len(new_article_info)

There are 441 articles we have already looked at


In [72]:
# Must now manually add abstracts for papers that do not have a pmid
to_add_title = ['The spatial pattern of basal ganglia network: A resting state fMRI study',
                'Task switching processes',
                'Cognitive control in depression and anxiety: Out of control? ',
                'Lateral and Dorsomedial Prefrontal Cortex and the Control of Cognition',
                'Functional MRI of brain activity during response inhibition in children',
                'Emotion, attention, and effortful control in 24-month-old very preterm and full-term children',
                'Executive Difficulties in Developmental Coordination Disorder: Methodological Issues and Future Directions',
                'Executive function: Reflection, iterative reprocessing, complexity, and the developing brain.',
                'Kindergarten Self‐Regulation As a Predictor of Body Mass Index and Sports Participation in Fourth Grade Students'
                ]
to_add_authors = ['X. Wen, L. Yao, T. Fan, X. Wu and J. Liu','Jamadar, S., Thienel, R., & Karayanidis, F.','Paulus, M. P.','Michalakis Petrides','Y.AbdullaevaJ.BrucebP.A.Fisherab',
                  'Lejeune, Fleur, Borradori Tolsa, Cristina, Bickle Graz, Myriam, Hüppi, Petra Susan, Barisnikov, Koviljka','    Hayley C. Leonard & Elisabeth L. Hill ','Zelazo, P. D.',
                  'G. Piche ́, C. Fitzpatrick, and L. S. Pagani'
                 ]
to_add_pmid = ['-','-','-','-','-','-','-','-','-']
to_add_keywords = ['-','-','-','-','-','-','-','-','-']
to_add_pubdate = ['2012-08-23','2015','2015','2015','2012','2015','2015','2015','2012']
to_add_abstract = ['Basal ganglia, consisting of the putamen, caudate nucleus, pallidum, substantia nigra and subthalamic nucleus, are associated with a variety of functions, including motor, cognitive, motivational, and emotional processes, and play an important role in numerous neurological and psychiatric disorders. Here, we utilized two kinds of resting state functional connectivity techniques: independent component analysis (ICA) and regions of interest (ROI) based correlation analysis, to find the spatial pattern of basal ganglia network through functional magnetic resonance imaging (fMRI) examination during rest. fMRI data were acquired in twenty-one healthy subjects. The results identified the existence of resting state network in basal ganglia and thalamus. Meantime, our study highlighted that caudate nucleus was also a part of this network. Compared with ROI-based analysis, the approach of ICA was more suited to detect this network.',
                'Task switching is a core component of cognitive control processes that enable goal-directed behavior and are supported by frontoparietal networks. Neuropsychological switching tasks are sensitive to damage in these networks, but do not specifically target control processes involved in task switching. Experimental task switching paradigms identify and differentiate between proactive control processes that prepare the system for the upcoming target and reactive control processes that resolve interference after target onset. We review electrophysiological and brain imaging studies that define the proactive and reactive cognitive control processes involved in task switching and the frontoparietal networks that support them.',
                'The recent literature on cognitive control dysfunctions in depression and anxiety is reviewed with particular emphasis on evidence for proactive and reactive control deficits. Individuals with depression and anxiety show few, if any, specific control deficits, however, there is evidence for non-specific interference that can be related to problems with rumination, worrying, attention and inhibition. Moreover, both electrophysiological and neuroimaging studies provide strong evidence for altered processing during cognitive control paradigms in depression and anxiety. Thus a layered model of control deficits is proposed, which presumes that agent-specific, task-irrelevant factors contribute to cognitive control processing alterations in anxiety and depression. A Bayesian Ideal Observer model is suggested as a possible approach to better disambiguate the dysfunctional processes in depression and anxiety. (PsycINFO Database Record (c) 2017 APA, all rights reserved)',
                'The prefrontal cortical region comprises several higher-order control processes and is functionally organized along both rostral–caudal and dorsal–ventral axes. The caudal dorsolateral prefrontal region that lies immediately anterior to the motor region is involved in higher-order control processes that regulate the attentional selection among multiple competing environmental stimuli. Medial to this region, the cingulate-prefrontal region contributes to critical evaluation of action outcomes, often referred to as performance monitoring. The mid-dorsolateral prefrontal region contributes to the monitoring of events in working memory, which, in interaction with posterior parietal cortex, allow for the cognitive manipulation of events in working memory. The ventrolateral prefrontal region, which in the language-dominant hemisphere plays a critical role in language production, also regulates effortful controlled retrieval from memory.',
                'Impulse control (or response inhibition) is an important cognitive function involved in many developmental disorders. Recent neuroimaging studies have started to uncover the underlying neuroanatomy of inhibitory control, which develops in children until late adolescence. We studied brain activations in 19 children (age 9–12 yrs). They performed a go/no-go task while brain activity was measured by a 3 T fMRI in an event-related design (when different trial types were presented in a random unpredictable order). Children saw single digits on a monitor and had to press a button in response to every digit except one of the digits designated as a no-go target. There were 4 types of trials: go trials, and no-go trials following 1, 3 or 5 go trials. Incorrect go trials were excluded from the analysis. No-go trials were divided into correct and incorrect groups for a separate analysis. Structural MRI T1 images with 1 mm resolution were averaged across all subjects using FSL and registered to MNI space to be used as an anatomical template for displaying functional activations. Statistical analyses of fMRI data based on general linear modeling were conducted using FSL. Here we report preliminary analysis of the data of this ongoing study. Correct no-go trials (where children successfully inhibited the prepotent button press response) were compared to go trials and revealed significant activations in the right frontal cortex (Brodmann areas — BAs 6, 44 and 45), the anterior cingulate (BA 24), the left and right superior frontal gyri (BAs 8 and 9), the right middle and superior temporal gyri, and the right parietal lobe supramarginal gyrus. Erroneous no-go trials (where children failed to inhibit a prepotent response and pressed the button), when compared to the same go trials, were accompanied by significant activations in the right frontal cortex (BAs 6 and 44) extending into the right insula (BA 13); the anterior cingulate (BA 25); the right prefrontal cortex (BAs 9 and 47); the left prefrontal cortex (BA 45); the right parietal lobe precuneous region (BAs 7 and 31); the right superior temporal gyrus (BA 38); the right and left occipital lobes including the lingual and fusiform gyri (BA 19); the right parahippocampal gyrus (BA 19); and the left and right insula (BA 13). Incorrect no-go trials differed from the correct no-go trials in significantly stronger activations in occipital lobe cuneus and precuneus bilaterally. Correct no-go trials differed from incorrect no-go trials in significantly stonger activations in the lentiform nucleus including the putamen and lateral globus pallidus bilaterally. The no-go trials following 5 go trials differed from no-go trials following 1 go trial in significantly stronger activations in the right middle frontal gyrus (BA 10); the right and left superior parietal lobules (BA 7); and the right and left middle occipital gyri (BA 19). These results confirm the importance of the right prefrontal cortex, as well as the insula and anterior cingulate in response inhibition, and extend the previous neuroimaging studies of response inhibition in children. These results also provide a foundation for our current and future clinical studies of response inhibition in at-risk children.',
                'The literature reports behavioral and socio-emotional problems in children born preterm that persist throughout adolescence and early adulthood. However, no study has simultaneously investigated emotion, attention, and effortful control. In the present study, we compared these abilities between children born very preterm (<29 weeks of gestation) and full-term children at 24 months of age by parental questionnaire and experimental design. Results on the questionnaire showed that very preterm children were rated by parents as having a higher level of negative affect and lower sustained attention than full-term children. Results on the experimental tasks revealed a distinct attention pattern between the two groups: The full-term children showed a peak of attention in the second trial while preterm children exhibited an unchanged level of attention throughout the task. The preterm children also exhibited greater difficulties in maintaining inhibitory control compared with full-term children. Taken together, the results observed in very preterm children clearly showed difficulties in key abilities which allow a voluntary self-regulation behavior and consequently, they should be considered to improve early intervention strategies. ',
                'Motor skills and cognition have often been studied separately, but there is increasing understanding of the close relationship between these abilities over development. Motor coordination difficulties are central to the diagnosis of developmental coordination disorder (DCD), and recent evidence suggests that certain cognitive processes, known as ‘executive functions’, may be affected in individuals with this neurodevelopmental disorder. In this article, we review the research concerning executive functions in DCD, considering behavioural, neuroimaging and questionnaire studies of a range of processes. We highlight methodological issues relating to our current understanding of executive functioning difficulties in DCD, including problems with interpretation of results based on the tasks used. We suggest future directions for research in this area, including the relationship of laboratory research to interventions within ‘real-world’ contexts.',
                'Key executive function (EF) skills (cognitive flexibility, working memory, inhibitory control) are essential for goal-directed problem solving and reflective learning. This article describes executive function (EF) and its development from the perspective of the Iterative Reprocessing (IR) model. According to this model, reflection, or the reflective reprocessing of information prior to responding, provides a foundation for the control of attention—flexibly, over time, and selectively (i.e., cognitive flexibility, working memory, and inhibitory control). This goal-directed modulation of attention is typically verbally mediated and involves the formulation and maintenance in working memory of explicit action-oriented rules. The development of EF is made possible, in part, by increases in the efficiency of reflective reprocessing which allow for increases in the hierarchical complexity of the rules that can be used to characterize problems and select context-appropriate rules for responding. Research designed to test the model indicates that a brief intervention targeting reflection and rule use leads to improved EF and theory of mind, and produces corresponding changes in neural function. (PsycINFO Database Record (c) 2018 APA, all rights reserved)',
                'Identifying early precursors of body mass index (BMI) and sports participation represents an important concern from a public health perspective and can inform the development of preventive interventions. This article examines whether kindergarten child self‐regulation, as measured by classroom engagement and behavioral regulation, predicts healthy dispositions in fourth grade. To address this objective, secondary analyses were conducted using prospective‐longitudinal data from 966 children followed by the Quebec Longitudinal Study of Child Development. Self‐regulatory skills, including classroom engagement and behavioral regulation, were measured by kindergarten teachers. Greater self‐regulatory skills predicted lower BMI and greater parent‐reported child sports participation, after controlling for a number of potentially confounding child and family characteristics. This article suggests that assessing kindergarten self‐regulatory capacities may help identify children at risk of developing unhealthy dispositions and behaviors in middle childhood.']

# Put into dataframe
to_add_prev = pd.DataFrame({'title':to_add_title,'authors':to_add_authors,'pmid':to_add_pmid,'keywords':to_add_keywords,'pubdate':to_add_pubdate,'abstract':to_add_abstract})

In [73]:
new_article_info = pd.concat([new_article_info,to_add_prev]).reset_index()
plus_manuals = len(new_article_info)

In [87]:
print(f"""
There were {all_prev} overall
There were {after2010_prev} after articles from before 2010 were removed
There were {fin_prev} articles overall after duplicates were removed
There are {n_overlap} articles we have already looked at
That leaves {n_new} article abstracts to read
Now manually add leftover for a total of: {plus_manuals}
""")


There were 3189 overall
There were 987 after articles from before 2010 were removed
There were 908 articles overall after duplicates were removed
There are 441 articles we have already looked at
That leaves 467 article abstracts to read
Now manually add leftover for a total of: 476



In [88]:
new_article_info['rater'] = '-'

In [89]:
# Randomly shuffle the dataframe so that they are in no particular order for each rater
article_info_rater1 = new_article_info.sample(frac=1).reset_index(drop=True)
article_info_rater2 = new_article_info.sample(frac=1).reset_index(drop=True)

In [90]:
# save thse dataframe for both raters
save_dir = opj(os.getcwd(), 'notebooks','to_check_prev_articles')
#article_info_rater1.to_excel(opj(save_dir, 'prevs_to_check_mck.xlsx'), sheet_name = 'pmid_mck') # DONT RUN AGAIN
#article_info_rater2.to_excel(opj(save_dir, 'prevs_to_check_sct.xlsx'), sheet_name = 'pmid_sct') # DONT RUN AGAIN

### Load in checked previous meta articles and combine any new ones with the original found articles

In [75]:
# load in pmids of new abstracts to check through
extra_full_texts_dir = opj(os.getcwd(), 'notebooks/checked_prev_articles')

checked_dois_mck = pd.read_excel(opj(extra_full_texts_dir,'prevs_checked_mck.xlsx'),index_col=0,keep_default_na=False)
checked_dois_mck.set_index('index',inplace=True)
checked_dois_mck = checked_dois_mck.rename(columns={'rater':'rater1'})

checked_dois_sct = pd.read_excel(opj(extra_full_texts_dir,'prevs_checked_sct.xlsx'),index_col=0,keep_default_na=False)
checked_dois_sct.set_index('index',inplace=True)
checked_dois_sct = checked_dois_sct.reindex(checked_dois_mck.index) # reindex so they are the same order
checked_dois_sct = checked_dois_sct.rename(columns={'rater':'rater2'})

In [76]:
# Print some descriptive checks before calculating inter rater reliability (IRR)
print('Rater 1 overall stats:')
print('no. ones = ' + str(len(checked_dois_mck.loc[checked_dois_mck['rater1']==1])))
print('no. twos = ' + str(len(checked_dois_mck.loc[checked_dois_mck['rater1']==2])))
print('no. threes = ' + str(len(checked_dois_mck.loc[checked_dois_mck['rater1']==3])))
print('no. fours = ' + str(len(checked_dois_mck.loc[checked_dois_mck['rater1']==4])))
print('no. misses = ' + str(len(checked_dois_mck.loc[checked_dois_mck['rater1']=='-'])))

print('')

print('Rater 2 overall stats:')
print('no. ones = ' + str(len(checked_dois_sct.loc[checked_dois_sct['rater2']==1])))
print('no. twos = ' + str(len(checked_dois_sct.loc[checked_dois_sct['rater2']==2])))
print('no. threes = ' + str(len(checked_dois_sct.loc[checked_dois_sct['rater2']==3])))
print('no. fours = ' + str(len(checked_dois_sct.loc[checked_dois_sct['rater2']==4])))
print('no. misses = ' + str(len(checked_dois_sct.loc[checked_dois_sct['rater2']=='-'])))

Rater 1 overall stats:
no. ones = 0
no. twos = 0
no. threes = 476
no. fours = 0
no. misses = 0

Rater 2 overall stats:
no. ones = 0
no. twos = 0
no. threes = 476
no. fours = 0
no. misses = 0


In [137]:
# Both raters marked all abstracts as '3', so IRR is 1.
# No new full articles needed to add to the list. 

## Now, download full texts of all of the articles of interest

In [77]:
# list of full texts = full_texts dataframe
# Take a look at it:
print(f'There are {len(full_texts)} articles to get full texts of')
full_texts.head(3)

There are 755 articles to get full texts of


title  \
pmid                                                                                                                           
22056967                        Functional connectivity of dissociation in patients with psychogenic non-epileptic seizures.   
25698959    Effect of foreknowledge on neural activity of primary "go" responses relates to response stopping and switching.   
20498351  Moment-to-moment fluctuations in fMRI amplitude and interregion coupling are predictive of inhibitory performance.   

                                                                                                                                         authors  \
pmid                                                                                                                                               
22056967  van der Kruijs, SJ., Bodde, NM., Vaessen, MJ., Lazeron, RH., Vonck, K., Boon, P., Hofman, PA., Backes, WH., Aldenkamp, AP., Jansen, JF   
25698959                                                                         Xu, B., Levy, S., Butman, J., Pham, D., Cohen, LG., Sandrini, M   
20498351                                                                                                                  Padmala, S., Pessoa, L   

                                                                        keywords  \
pmid                                                                               
22056967                                                 Article has no keywords   
25698959  fMRI", "foreknowledge", "impulse", "response inhibition", "stop-signal   
20498351                                                 Article has no keywords   

             pubdate  \
pmid                   
22056967  2011-11-08   
25698959  2015-02-24   
20498351  2010-05-26   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                         abstract  \
pmid                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                
22056967  Psychogenic non-epileptic seizures (PNES) resemble epileptic seizures, but lack epileptiform brain activity. Instead, the cause is assumed to be psychogenic. A

In [145]:
# First convert all pmids to DOIs so we can download PDFs easily
import metapub

# create empty dataframe to append to
DOIframe = pd.DataFrame({'pmids': full_texts.index, 'DOIs':'-'})

# loop over pmids to convert to DOIs
for pmid in DOIframe.pmids:
    try:
        DOIframe.loc[DOIframe.pmids==pmid,'DOIs'] = metapub.convert.pmid2doi(pmid)
    except:
        print(DOIframe.loc[DOIframe.pmids==pmid])
        continue

       pmids DOIs
30  24968573    -
        pmids DOIs
152  30125245    -
        pmids DOIs
219  22147454    -
        pmids DOIs
480  21720977    -


In [146]:
# Check which DOIs could not be identifed and manually download their papers
manual_download = DOIframe.loc[DOIframe.DOIs=='-'].pmids
manual_download

30     24968573
152    30125245
219    22147454
480    21720977
Name: pmids, dtype: object

In [147]:
print(f"""
There were {len(full_texts)} articles to get the full texts of
{len(DOIframe.loc[DOIframe['DOIs']!='-',])} DOIs were found
{len(manual_download)} of them will need to be manually downloaded
Quick check: no. found {len(DOIframe.loc[DOIframe['DOIs']!='-',])} + no. manual {len(manual_download)} should equal: {len(full_texts)}
""")


There were 755 articles to get the full texts of
751 DOIs were found
4 of them will need to be manually downloaded
Quick check: no. found 751 + no. manual 4 should equal: 755



In [148]:
# Save the DOIframe dataframe so that the scihub/metapub code does not need to be run again
#DOIframe.to_excel(opj(os.getcwd(), 'notebooks', 'dois_and_pmids_full_texts','dois_full_texts.xlsx'), sheet_name = 'pmids-dois') # code already run, don't run again

In [170]:
# Now download full texts via sci hub including other references from the previous reviews
from scidownl.scihub import *

# What folder to save in?
out_dir = opj(os.getcwd(), 'save_pdfs','full_texts_to_check')

# create a dataframe for pdfs that couldn't be downloaded
failed_frame = pd.DataFrame(columns=['pmids','DOIs'])

# loop over DOIs from dataframe
for doi in DOIframe['DOIs'].loc[DOIframe['DOIs']!='-']: 
    # save pdfs
    try:
        #SciHub(doi, out_dir).download(choose_scihub_url_index=3) # already run, don't run again
    except:
        failed_frame = failed_frame.append(DOIframe.loc[DOIframe.DOIs==doi,])
        continue

[INFO] Choose the available link 3: https://sci-hub.se
[INFO] PDF url -> 
	http://moscow.sci-hub.se/2073/86707362af688bdf56a6338c941af8ac/vanderkruijs2011.pdf
[INFO] Article title -> 
	Functional connectivity of dissociation in patients with psychogenic non-epileptic seizures
[INFO] Verifying...
[INFO] Verification success.
[100%] Progress: 750938 / 750938
[INFO] Done.                                             
[INFO] Choose the available link 3: https://sci-hub.se
[INFO] PDF url -> 
	http://twin.sci-hub.se/7016/6199045992d5402599d5d16ee4a285f2/xu2015.pdf
[INFO] Article title -> 
	Effect of foreknowledge on neural activity of primary â€œgoâ€ responses relates to response stopping and switching
[INFO] Verifying...
[INFO] Verification success.
[100%] Progress: 1734904 / 1734904
[INFO] Done.                                             
[INFO] Choose the available link 3: https://sci-hub.se
[INFO] PDF url -> 
	http://moscow.sci-hub.se/1084/b6c9d467047ff254d23c28410405fe84/padmala2010.pd

[INFO] Verification success.
[100%] Progress: 386005 / 386005
[INFO] Done.                                             
[INFO] Choose the available link 3: https://sci-hub.se


[INFO] PDF url -> 
	http://zero.sci-hub.se/4343/b7bfa5c50db0a7a515ae7a9b4b4516aa/loitfelder2011.pdf
[INFO] Article title -> 
	Reorganization in cognitive networks with progression of multiple sclerosis  Insights from fMRI
[INFO] Verifying...
[INFO] Verification success.
[100%] Progress: 1475077 / 1475077
[INFO] Done.                                             
[INFO] Choose the available link 3: https://sci-hub.se
[INFO] PDF url -> 
	http://twin.sci-hub.se/7096/b6e3b179f48fb9bb298ec79ff5a3b8c0/davidow2019.pdf
[INFO] Article title -> 
	davidow2019
[INFO] Verifying...
[INFO] Verification success.
[100%] Progress: 1254864 / 1254864
[INFO] Done.                                             
[INFO] Choose the available link 3: https://sci-hub.se
[INFO] PDF url -> 
	http://twin.sci-hub.se/5886/512992a015a898e7d4865621ccfcde8d/braem2016.pdf
[INFO] Article title -> 
	braem2016
[INFO] Verifying...
[INFO] Verification success.
[100%] Progress: 2096185 / 2096185
[INFO] Done.                      

[INFO] Verification success.
[100%] Progress: 754123 / 754123
[INFO] Done.                                             
[INFO] Choose the available link 3: https://sci-hub.se


[INFO] PDF url -> 
	http://sci-hub.se/downloads/2019-10-15/27/limbrick-oldfield2019.pdf
[INFO] Article title -> 
	Neural and neurocognitive markers of vulnerability to gambling disorder  a study of unaffected siblings
[INFO] Verifying...
[INFO] Verification success.
[100%] Progress: 1351466 / 1351466
[INFO] Done.                                             
[INFO] Choose the available link 3: https://sci-hub.se
[INFO] PDF url -> 
	http://dacemirror.sci-hub.se/journal-article/77951dce6ed1ca424662e918c77140ad/thomaes2012.pdf
[INFO] Article title -> 
	Treatment effects on insular and anterior cingulate cortex activation during classic and emotional Stroop interference in child abuse-related complex post-traumatic stress disorder
[INFO] Verifying...
[INFO] Verification success.
[100%] Progress: 271594 / 271594
[INFO] Done.                                             
[INFO] Choose the available link 3: https://sci-hub.se
[INFO] PDF url -> 
	http://twin.sci-hub.se/5845/5733d248597c36a6d61fe

...

[INFO] Verification success.
[100%] Progress: 861999 / 861999
[INFO] Done.                                             
[INFO] Choose the available link 3: https://sci-hub.se
[INFO] PDF url -> 
	http://zero.sci-hub.se/5235/2910d6898956ddb48f8c51740c62b3ad/luethi2016.pdf
[INFO] Article title -> 
	Motivational incentives lead to a strong increase in lateral prefrontal activity after self-control exertion
[INFO] Verifying...
[INFO] Verification success.
[100%] Progress: 5301773 / 5301773
[INFO] Done.                                             
[INFO] Choose the available link 3: https://sci-hub.se
[INFO] PDF url -> 
	http://dacemirror.sci-hub.se/journal-article/75206c3f31b27395b724b1424a9248d2/harle2014.pdf
[INFO] Article title -> 
	Altered Neural Processing of the Need to Stop in Young Adults at Risk for Stimulant Dependence
[INFO] Verifying...
[INFO] Verification success.
[100%] Progress: 2380347 / 2380347
[INFO] Done.                                             
[INFO] Choose the avai

[INFO] Verification success.
[100%] Progress: 230389 / 230389
[INFO] Done.                                             
[INFO] Choose the available link 3: https://sci-hub.se


[INFO] PDF url -> 
	http://cyber.sci-hub.se/MTAuMTE3Ni9hcHBpLmFqcC4yMDExLjA5MTIxODEy/shin2011.pdf
[INFO] Article title -> 
	Exaggerated Activation of Dorsal Anterior Cingulate Cortex During Cognitive Interference  A Monozygotic Twin Study of Posttraumatic Stress Disorder
[INFO] Verifying...
[INFO] Verification success.
[100%] Progress: 819979 / 819979
[INFO] Done.                                             
[INFO] Choose the available link 3: https://sci-hub.se
[INFO] PDF url -> 
	http://cyber.sci-hub.se/MTAuMTA4OS9icmFpbi4yMDE4LjA2MTk=/stange2018.pdf
[INFO] Article title -> 
	Predictors of Attrition in Longitudinal Neuroimaging Research  Inhibitory Control, Head Movement, and Resting-State Functional Connectivity
[INFO] Verifying...
[INFO] Verification success.
[100%] Progress: 321215 / 321215
[INFO] Done.                                             
[INFO] Choose the available link 3: https://sci-hub.se
[INFO] PDF url -> 
	http://moscow.sci-hub.se/4340/38056b216a1d1c61a7c0150a40948a

[INFO] Verification success.
[100%] Progress: 422373 / 422373
[INFO] Done.                                             
[INFO] Choose the available link 3: https://sci-hub.se
[INFO] PDF url -> 
	http://dacemirror.sci-hub.se/journal-article/38d7b017d74d24060d6c735cab44985c/aarts2011.pdf
[INFO] Article title -> 
	Attentional Control in Anterior Cingulate Cortex Based on Probabilistic Cueing
[INFO] Verifying...
[INFO] Verification success.
[100%] Progress: 428731 / 428731
[INFO] Done.                                             
[INFO] Choose the available link 3: https://sci-hub.se
[INFO] PDF url -> 
	http://dacemirror.sci-hub.se/journal-article/2697ef287efb3a6d02dc78de07c05315/golm2016.pdf
[INFO] Article title -> 
	Tinnitus- related distress  evidence from fMRI of an emotional stroop task
[INFO] Verifying...
[INFO] Verification success.
[100%] Progress: 1853593 / 1853593
[INFO] Done.                                             
[INFO] Choose the available link 3: https://sci-hub.se
[INF

[INFO] Verification success.
[100%] Progress: 2226516 / 2226516
[INFO] Done.                                             
[INFO] Choose the available link 3: https://sci-hub.se
[INFO] PDF url -> 
	http://zero.sci-hub.se/2447/123dbfb3de09fa3c06fbfa02debab035/krebs2013.pdf
[INFO] Article title -> 
	Picture novelty attenuates semantic interference and modulates concomitant neural activity in the anterior cingulate cortex and the locus coeruleus
[INFO] Verifying...
[INFO] Verification success.
[100%] Progress: 781282 / 781282
[INFO] Done.                                             
[INFO] Choose the available link 3: https://sci-hub.se
[INFO] PDF url -> 
	http://cyber.sci-hub.se/MTAuMTAxNi9qLmRydWdhbGNkZXAuMjAxMS4xMC4wMDI=/devito2012.pdf
[INFO] Article title -> 
	A preliminary study of the neural effects of behavioral therapy for substance use disorders
[INFO] Verifying...
[INFO] Verification success.
[100%] Progress: 564234 / 564234
[INFO] Done.                                           

In [171]:
# Manually add these 
failed_frame

pmids                                  DOIs
64   30094335           10.1523/ENEURO.0035-17.2018
91   24107763                  10.4088/JCP.12m08020
207  23772336              10.4172/2155-6105.S3-002
212  29620519                    10.1503/jpn.170116
290  27575858                    10.1503/jpn.150335
378  28234209                    10.1503/jpn.160081
412  28004954                    10.1037/bne0000175
465  22775772                      10.1037/a0029092
517  26402462                   10.7554/eLife.08723
613  22246362  10.3969/j.issn.1672-7347.2011.12.008
666  22440976          10.1097/WNR.0b013e3283525a95

In [169]:
# Manually download the 4 articles without DOIs
# These articles are:
full_texts.loc[full_texts.index.isin(list(manual_download)),]

# Only 1 of these (30125245) were added as 3 were not in english (one indian, japanese & spanish)

title  \
pmid                                                                                                                                                                                           
24968573                                                                                                  Mechanism of selective attention: fMRI study of face-word Stroop task performance.   
30125245                                                                                     Neurocognitive, emotional and neuroendocrine correlates of exposure to sexual assault in women.   
22147454                                                                                                                                            [Frontal lobes and inhibitory function].   
21720977  [Involvement of the thalamic-cortical-striatal circuit in patients with obsessive-compulsive disorder during an inhibitory control task with reward and punishment contingencies].   

                                                                                                                                                                                                   authors  \
pmid                                                                                                                                                                                                         
24968573                                                                                                                                    Vivekananth, S., Sood, SK., Senthil Kumaran, S., Srivastava, A   
30125245  Quidé, Y., Cléry, H., Andersson, F., Descriaud, C., Saint-Martin, P., Barantin, L., Gissot, V., Carrey Le Bas, MP., Osterreicher, S., Dufour-Rainfray, D., Brizard, B., Ogielska, M., El-Hage, W   
22147454                                                                                                                                                                                        Konishi, S   
21720977                                                                                  Pena-Garijo, J., Barros-Loscertales, A., Ventura-Campos, N., Ruipérez-Rodríguez, MÁ., Edo-Villamon, S., Ávila, C   

                         keywords     pubdate  \
pmid                                            
24968573  Article has no keywords  2014-06-28   
30125245  Article has no keywords  2018-08-21   
22147454  Article has no keywords  2011-12-08   
21720977  Article has no keywords  2011-07-02   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                         abstract  \
pmid                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                 

NOTES ON MANUALLY ADDED papers:
- pmid's 30125245 and 29620519 are the same paper. Only add one. 
- pmid's 24968573, 22147454, 21720977, 22440976 are not in English (indian, japanese, spanish & chinese)
- So only needed to manually add 10 out of the 15 articles. 

In [80]:
# Fetch the number of pdfs downloaded to check it worked
out_dir = opj(os.getcwd(), 'save_pdfs','full_texts_to_check')
check_pdf = glob.glob(opj(out_dir,'*'))
print(f"Number of full texts ({len(check_pdf)}) should be the same as {len(full_texts)} - 5")

Number of full texts (750) should be the same as 755 - 5


######### ALL FULL TEXTS ARE DOWNLOADED ########

As there are 750 full texts, raters 1 and 2 will take half each

In [89]:
# list all of the full texts for the raters to go through

# THIS IS ALREADY RUN, DON'T RUN AGAIN

all_fulls = glob.glob(opj(os.getcwd(), 'save_pdfs','full_texts_to_check','*'))
random.shuffle(all_fulls) # mix up the order of full texts

# Give half of all full texts to rater 1
all_fulls_mck = all_fulls[:(len(all_fulls)//2)]
# move to new folder
for i in all_fulls_mck:
    old_loc = i.split('/')
    old_loc[-2] = 'full_texts_mck'
    new_loc = '/'.join(old_loc)
    #os.rename(i,new_loc)

# give other half of reviews to rater 2
all_fulls_sct = all_fulls[(len(all_fulls)//2):]
# move to new folder
for i in all_fulls_sct:
    old_loc = i.split('/')
    old_loc[-2] = 'full_texts_sct'
    new_loc = '/'.join(old_loc)
    #os.rename(i,new_loc)

In [90]:
# Make sure PDFs were moved correctly
half_fulls_mck = glob.glob(opj(os.getcwd(), 'save_pdfs','full_texts_mck','*'))
half_fulls_sct = glob.glob(opj(os.getcwd(), 'save_pdfs','full_texts_sct','*'))

print(f'Rater 1 has {len(half_fulls_mck)} full texts to read')
print(f'Rater 2 has {len(half_fulls_sct)} full texts to read')

Rater 1 has 375 full texts to read
Rater 2 has 375 full texts to read


Count how many included by each rater in the final sample.

In [8]:
CheckedHalfFullsMckYes = glob.glob(opj(os.getcwd(), 'finished_fulltexts','mck','yes_mck','*'))
CheckedHalfFullsMckNo = glob.glob(opj(os.getcwd(), 'finished_fulltexts','mck','no_mck','*'))

CheckedHalfFullsSctYes = glob.glob(opj(os.getcwd(), 'finished_fulltexts','sct','yes_sct','*'))
CheckedHalfFullsSctNo = glob.glob(opj(os.getcwd(), 'finished_fulltexts','sct','no_sct','*'))

print(f"""
Rater 1 included {len(CheckedHalfFullsMckYes)} full texts
Rater 2 included {len(CheckedHalfFullsSctYes)} full texts
Rater 1 removed {len(CheckedHalfFullsMckNo)} full texts
Rater 2 removed {len(CheckedHalfFullsSctNo)} full texts

Overall, {len(CheckedHalfFullsMckYes)+len(CheckedHalfFullsSctYes)} studies were elegible
Overall, {len(CheckedHalfFullsMckNo)+len(CheckedHalfFullsSctNo)} studies were not elegible
""")


Rater 1 included 52 full texts
Rater 2 included 66 full texts
Rater 1 removed 322 full texts
Rater 2 removed 308 full texts

Overall, 118 studies were elegible
Overall, 630 studies were not elegible



######### NOTEBOOK FINISHED #############

# ------------------------------------ Random code ---------------------------------------

In [ ]:
import re

#sentence = "Rapunzel/NNP Sheila/NNP let/VBD down/RP her/PP$ long/JJ golden/JJ hair/NN in Yasir/NNP"
([^\s]+)
tes = re.findall(r'PMid:(\w+)', check) # this finds number after 'PMid:' in chunk of text
for i in tes:
    print(i)

In [ ]:
for j in article_info.pmid:
    dois_to_add_sct.loc[dois_to_add_sct.pmid==j,'study'] = article_info.loc[article_info.pmid==j,'authors'].to_string(index=False) + article_info.pubdate[article_info.pmid==j].to_string(index=False) + article_info.title[article_info.pmid==j].to_string(index=False)

In [97]:
pubmed = pm.PubMed(tool="MyTool", email = 'scott@leeclan.net')

# loop over pmids of all found meta-analyses
#for pmid_args in reviews.index[0]:
    
pmid_args = reviews.index[1]
    
results = pubmed.query(query=pmid_args, max_results=2) # run search query

lengthable = pubmed.query(query=pmid_args, max_results=2) # non-elegant method to measure length of results

len_of_results = sum(1 for x in lengthable) # only way to get length of results output

if len_of_results > 1: # skip this PMID query search if more than one article comes up
    duplicate_checker = duplicate_checker.append(pmid_args)
    #continue
elif len_of_results == 0:
    print(f"PMID: {pmid_args} not found")

for article in results: # loop over all found articles

    print(article)
    # we only want to reference list from each result

In [35]:
pm.read_records(article.toJSON)

AttributeError: module 'pymed' has no attribute 'read_records'

In [38]:
for i in article.xml[0]:
    print('i' + str(i))
    for j in i:
        print('j'+str(j))
        for k in j:
            print('k'+str(k))
            for m in k:
                print('m'+str(m))

i<Element 'PMID' at 0x1a23a7f5e8>
i<Element 'DateCompleted' at 0x1a23a7f868>
j<Element 'Year' at 0x1a23a7fa98>
j<Element 'Month' at 0x1a23a7f4a8>
j<Element 'Day' at 0x1a23a7fb38>
i<Element 'DateRevised' at 0x1a23a7f098>
j<Element 'Year' at 0x1a23a7fdb8>
j<Element 'Month' at 0x1a23a7fd18>
j<Element 'Day' at 0x1a23a7f458>
i<Element 'Article' at 0x1a23a7fea8>
j<Element 'Journal' at 0x1a23a7f1d8>
k<Element 'ISSN' at 0x1a23a7f048>
k<Element 'JournalIssue' at 0x1a23a7fae8>
m<Element 'Volume' at 0x1a23a7fd68>
m<Element 'Issue' at 0x1a23a7f2c8>
m<Element 'PubDate' at 0x1a23a7f598>
k<Element 'Title' at 0x1a23a7f4f8>
k<Element 'ISOAbbreviation' at 0x1a23a7fb88>
j<Element 'ArticleTitle' at 0x1a23a7fa48>
j<Element 'Pagination' at 0x1a23a7ff48>
k<Element 'MedlinePgn' at 0x1a23a7fc78>
j<Element 'ELocationID' at 0x1a23a7f8b8>
j<Element 'ELocationID' at 0x1a23a7fe08>
j<Element 'Abstract' at 0x1a23a7f228>
k<Element 'AbstractText' at 0x1a23a7f958>
k<Element 'CopyrightInformation' at 0x1a23a7f6d8>
j<Elem

In [44]:
l = article.toDict()

In [45]:
l

{'pubmed_id': '30442541',
 'title': 'From One to Many: Representing Not Only Actions, but Interactions in the Brain.',
 'abstract': 'Observing others is a pervasive way of learning about the social world, but little is known about the neural correlates of observing more than one individual. A recent neuroimaging study demonstrates that activity in the human motor system tracks multiple actions and that anterior cingulate cortex is involved to monitor motor conflict.',
 'keywords': ['action observation',
  'motor system',
  'multiple actions',
  'social interactions'],
 'journal': 'Trends in cognitive sciences',
 'publication_date': datetime.date(2018, 11, 18),
 'authors': [{'lastname': 'Schilbach',
   'firstname': 'Leonhard',
   'initials': 'L',
   'affiliation': 'Max Planck Institute of Psychiatry, Kraepelinstr. 2-10, 80804 Munich, Germany. Electronic address: leonhard_schilbach@psych.mpg.de.'}],
 'methods': None,
 'conclusions': None,
 'results': None,
 'copyrights': 'Copyright © 201

In [138]:
for i in article.xml[0][0]:
    print(i)

In [139]:
print(article.toJSON())

{
    "abstract": "Observing others is a pervasive way of learning about the social world, but little is known about the neural correlates of observing more than one individual. A recent neuroimaging study demonstrates that activity in the human motor system tracks multiple actions and that anterior cingulate cortex is involved to monitor motor conflict.",
    "authors": [
        {
            "affiliation": "Max Planck Institute of Psychiatry, Kraepelinstr. 2-10, 80804 Munich, Germany. Electronic address: leonhard_schilbach@psych.mpg.de.",
            "firstname": "Leonhard",
            "initials": "L",
            "lastname": "Schilbach"
        }
    ],
    "conclusions": null,
    "copyrights": "Copyright \u00a9 2018 Elsevier Ltd. All rights reserved.",
    "doi": "10.1016/j.tics.2018.10.007",
    "journal": "Trends in cognitive sciences",
    "keywords": [
        "action observation",
        "motor system",
        "multiple actions",
        "social interactions"
    ],
    "

In [140]:
print(article.xml())

TypeError: 'xml.etree.ElementTree.Element' object is not callable

In [124]:
print(to_json)

<bound method PubMedArticle.toJSON of <pymed.article.PubMedArticle object at 0x1a26da7828>>


# Now start to download full texts as PDFs

In [ ]:
## 1st

## 1st: Download full texts of other meta-analyses to cross reference the used articles

In [148]:
# Download full texts of other meta-analyses on similar topics
# create empty dataframe to append to
DOIframe_metas = pd.DataFrame({'pmids': reviews.index, 'DOIs':'-'})

# loop over pmids to convert to DOIs
for pmid in DOIframe_metas.pmids:
    try:
        DOIframe_metas.loc[DOIframe_metas.pmids==pmid,'DOIs'] = metapub.convert.pmid2doi(pmid)
    except:
        print(DOIframe_metas.loc[DOIframe_metas.pmids==pmid])
        continue

In [47]:
# Now download full texts via sci hub for the reviews
from scidownl.scihub import *

# What folder to save in?
review_dir = '/Users/scotti/surfdrive/Projects/interference_in_the_subcortex/save_pdfs/reviews' 

# loop over DOIs from dataframe
for doi in DOIframe_metas.DOIs: 
    # save pdfs
    print(doi)
    # SciHub(doi, review_dir).download(choose_scihub_url_index=3) # already done don't do again

NameError: name 'DOIframe_metas' is not defined

## Then get references from all of the previous meta-analyses

- get all pubmed id's of all articles cited
- select only the ones that are published after 1 jan 2010
- exclude all pubmed id's that we've both agreed on not to include for full text in our initial query
- of the remaining pubmeds, exclude the ones that we've listed as reviews / meta analysis (label 4)
- of the remaining pubmeds, exclude the ones that we've already selected for full text inclusion
- that should leave only new pubmed id's

In [ ]:
# First loop over all of the previous meta-analyses to get their reference list
# Then extract DOIs of the reference list
# Then convert to pmids and append to a list to use later

# Instead of extracting references from pdfs, get the pmid id's of the meta-analyses and get the reference lists by spamming them again


In [55]:
import pdfx
import glob

# List the reviews to check paths to PDFs
extract_from = glob.glob(opj(review_dir,'*'))

# Create table to append all DOIs to 
extract_frame = pd.DataFrame({'review':[],'extract_doi':[]})

# Create list for reviews that encountered errors when extracting references
error_list = []

# Loop over the PDFs of all meta-analyses
for to_extract in extract_from:

    print(to_extract)
    
    try:
        pdf = pdfx.PDFx(to_extract)
    except:
        error_list.append(to_extract)
        
    metadata = pdf.get_metadata() # get metadata
    references_dict = pdf.get_references_as_dict() # get reference list
    
    # Append DOI references to dataframe to convert to pmid later
    extract_frame = extract_frame.append(pd.DataFrame({'review':to_extract,'extract_doi':references_dict['url']}))
            

2020-08-10 12:06:35 PinaColada.local root[1033] INFO xref found: pos=b'382771'
2020-08-10 12:06:35 PinaColada.local root[1033] INFO read_xref_from: start=382771, token=173
2020-08-10 12:06:35 PinaColada.local root[1033] INFO xref stream: objid=(0, 174), fields=1,3,2
2020-08-10 12:06:35 PinaColada.local root[1033] INFO trailer: {'Info': <PDFObjRef:172>, 'Filter': /'FlateDecode', 'Type': /'XRef', 'W': [1, 3, 2], 'Index': [0, 174], 'ID': [b'\x84\x11.Ja\xf6\x7f\x1c\xfa|PSw=/\xa3', b'\x999J+\x92\xf2\x8b6\xc2\x7f4\xd9\xd1\x16O\xed'], 'Root': <PDFObjRef:132>, 'Length': 516, 'Size': 174}
2020-08-10 12:06:35 PinaColada.local root[1033] INFO xref found: pos=b'382771'
2020-08-10 12:06:35 PinaColada.local root[1033] INFO read_xref_from: start=382771, token=173
2020-08-10 12:06:35 PinaColada.local root[1033] INFO xref stream: objid=(0, 174), fields=1,3,2
2020-08-10 12:06:35 PinaColada.local root[1033] INFO trailer: {'Info': <PDFObjRef:172>, 'Filter': /'FlateDecode', 'Type': /'XRef', 'W': [1, 3, 2],

/Users/scotti/surfdrive/Projects/interference_in_the_subcortex/save_pdfs/reviews/Functional MRI on executive functioning in aging and dementia  A scoping review of cognitive tasks.pdf


2020-08-10 12:06:35 PinaColada.local root[1033] INFO Pages: Kids=[<PDFObjRef:11>, <PDFObjRef:117>]
2020-08-10 12:06:35 PinaColada.local root[1033] INFO Pages: Kids=[<PDFObjRef:129>, <PDFObjRef:7>, <PDFObjRef:29>, <PDFObjRef:45>, <PDFObjRef:52>, <PDFObjRef:60>, <PDFObjRef:67>, <PDFObjRef:78>, <PDFObjRef:85>, <PDFObjRef:99>]
2020-08-10 12:06:35 PinaColada.local root[1033] INFO Page: {'Contents': [<PDFObjRef:5>, <PDFObjRef:133>, <PDFObjRef:6>], 'Type': /'Page', 'Resources': {'ExtGState': {'GS1': <PDFObjRef:12>}, 'ProcSet': [/'PDF', /'Text', /'ImageB', /'ImageC', /'ImageI'], 'Font': {'F10': <PDFObjRef:13>, 'F7': <PDFObjRef:33>, 'F8': <PDFObjRef:55>, 'F9': <PDFObjRef:134>, 'F1': <PDFObjRef:34>, 'F2': <PDFObjRef:15>, 'F3': <PDFObjRef:16>, 'F4': <PDFObjRef:35>, 'F5': <PDFObjRef:17>, 'F6': <PDFObjRef:18>}, 'XObject': {'Im1': <PDFObjRef:19>, 'Im2': <PDFObjRef:20>, 'Xi0': <PDFObjRef:1>, 'Xi1': <PDFObjRef:2>}, 'Properties': {'MC3': <PDFObjRef:135>, 'MC4': <PDFObjRef:136>, 'MC1': <PDFObjRef:137>, 

2020-08-10 12:06:35 PinaColada.local root[1033] INFO Processing xobj: <PDFStream(20): raw=7599, {'ColorSpace': /'DeviceRGB', 'Height': 42, 'Subtype': /'Image', 'Filter': /'FlateDecode', 'Type': /'XObject', 'Width': 315, 'BitsPerComponent': 8, 'Length': 7598}>
2020-08-10 12:06:35 PinaColada.local root[1033] INFO Processing xobj: <PDFStream(2): raw=50325, {'ColorSpace': [/'CalRGB', {'Gamma': [2.2, 2.2, 2.2], 'WhitePoint': [0.95043, 1, 1.09], 'Matrix': [0.41239, 0.21264, 0.01933, 0.35758, 0.71517, 0.11919, 0.18045, 0.07218, 0.9504]}], 'Intent': /'Perceptual', 'Subtype': /'Image', 'Height': 1004, 'Filter': /'FlateDecode', 'Type': /'XObject', 'Width': 1003, 'SMask': <PDFObjRef:1>, 'Length': 50324, 'BitsPerComponent': 8}>
2020-08-10 12:06:35 PinaColada.local root[1033] INFO Page: {'Contents': <PDFObjRef:9>, 'Type': /'Page', 'Resources': <PDFObjRef:10>, 'CropBox': [0, 0, 595.276, 782.362], 'Parent': <PDFObjRef:11>, 'Rotate': 0, 'MediaBox': [0, 0, 595.276, 782.362]}
2020-08-10 12:06:35 PinaCol

2020-08-10 12:06:36 PinaColada.local root[1033] INFO Processing xobj: <PDFStream(20): raw=7599, {'ColorSpace': /'DeviceRGB', 'Height': 42, 'Subtype': /'Image', 'Filter': /'FlateDecode', 'Type': /'XObject', 'Width': 315, 'BitsPerComponent': 8, 'Length': 7598}>
2020-08-10 12:06:36 PinaColada.local root[1033] INFO Processing xobj: <PDFStream(19): raw=388, {'Height': 108, 'Subtype': /'Image', 'Filter': /'CCITTFaxDecode', 'DecodeParms': {'Columns': 517, 'K': -1}, 'Type': /'XObject', 'Width': 517, 'ImageMask': True, 'BitsPerComponent': 1, 'Length': 387}>
2020-08-10 12:06:36 PinaColada.local root[1033] INFO Page: {'Contents': <PDFObjRef:61>, 'Type': /'Page', 'Resources': <PDFObjRef:62>, 'CropBox': [0, 0, 595.276, 782.362], 'Parent': <PDFObjRef:11>, 'Rotate': 0, 'MediaBox': [0, 0, 595.276, 782.362]}
2020-08-10 12:06:36 PinaColada.local root[1033] INFO Processing page: <PDFPage: Resources={'ExtGState': {'GS1': <PDFObjRef:12>}, 'ProcSet': [/'PDF', /'Text', /'ImageB', /'ImageC'], 'Font': {'F10': 

...

2020-08-10 12:46:26 PinaColada.local root[1033] INFO xref found: pos=b'160'
2020-08-10 12:46:26 PinaColada.local root[1033] INFO read_xref_from: start=160, token=/b'xref'
2020-08-10 12:46:26 PinaColada.local root[1033] INFO xref objects: {62: (None, 15, 0), 63: (None, 1110, 0), 64: (None, 1780, 0), 65: (None, 2153, 0), 66: (None, 36945, 0), 67: (None, 37442, 0), 68: (None, 37832, 0), 69: (None, 38242, 0), 70: (None, 50809, 0), 71: (None, 51160, 0), 72: (None, 51600, 0), 73: (None, 51887, 0), 74: (None, 52123, 0), 75: (None, 52458, 0), 76: (None, 52531, 0), 77: (None, 53183, 0), 78: (None, 53539, 0), 79: (None, 54066, 0), 80: (None, 60021, 0), 81: (None, 60487, 0), 82: (None, 60663, 0), 83: (None, 60948, 0), 84: (None, 61172, 0), 85: (None, 61520, 0), 86: (None, 61578, 0), 87: (None, 62051, 0), 88: (None, 62443, 0), 89: (None, 62840, 0), 90: (None, 68336, 0), 91: (None, 68662, 0), 92: (None, 69187, 0), 93: (None, 69526, 0), 94: (None, 72835, 0), 95: (None, 72873, 0), 96: (None, 81732, 0

2020-08-10 12:46:26 PinaColada.local root[1033] INFO get_font: create: objid=71, spec={'ToUnicode': <PDFObjRef:72>, 'Subtype': /'Type1', 'FontDescriptor': <PDFObjRef:73>, 'BaseFont': /'CGLBNH+AdvPSSym', 'Widths': [791, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 166], 'Encoding': <PDFObjRef:75>, 'Type': /'Font', 'FirstChar': 2, 'LastChar': 135}
2020-08-10 12:46:26 PinaColada.local root[1033] INFO get_font: create: objid=76, spec={'ToUnicode': <PDFObjRef:77>, 'Subtype': /'Type1', 'FontDescriptor': <PDFObjRef:78>, 'BaseFont': /'CGLBMG+AdvPS_TINR', 'Widths': [437, 270, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 

/Users/scotti/surfdrive/Projects/interference_in_the_subcortex/save_pdfs/reviews/Mapping numerical processing, reading, and executive functions in the developing brain  an fMRI meta-analysis of 52 studies including 842 children.pdf


2020-08-10 12:46:27 PinaColada.local root[1033] INFO Processing xobj: <PDFStream(65): raw=34628, {'Height': 174, 'BitsPerComponent': 8, 'Subtype': /'Image', 'Length': 34627, 'ColorSpace': /'DeviceRGB', 'Type': /'XObject', 'Filter': /'DCTDecode', 'Width': 3093}>
2020-08-10 12:46:27 PinaColada.local root[1033] INFO Page: {'Type': /'Page', 'Resources': <PDFObjRef:2>, 'MediaBox': [0, 0, 595.276, 841.89], 'Parent': <PDFObjRef:57>, 'Contents': <PDFObjRef:3>}
2020-08-10 12:46:27 PinaColada.local root[1033] INFO Processing page: <PDFPage: Resources={'ProcSet': [/'PDF', /'Text'], 'Font': {'F1': <PDFObjRef:91>, 'F3': <PDFObjRef:86>, 'F4': <PDFObjRef:66>, 'F5': <PDFObjRef:76>, 'F6': <PDFObjRef:71>, 'F7': <PDFObjRef:37>, 'F8': <PDFObjRef:40>}, 'ExtGState': {'GS1': <PDFObjRef:45>}}, MediaBox=[0, 0, 595.276, 841.89]>
2020-08-10 12:46:27 PinaColada.local root[1033] INFO render_contents: resources={'ProcSet': [/'PDF', /'Text'], 'Font': {'F1': <PDFObjRef:91>, 'F3': <PDFObjRef:86>, 'F4': <PDFObjRef:66>,

2020-08-10 12:46:28 PinaColada.local root[1033] INFO Page: {'Type': /'Page', 'Resources': <PDFObjRef:26>, 'MediaBox': [0, 0, 595.276, 841.89], 'Parent': <PDFObjRef:57>, 'Contents': <PDFObjRef:27>}
2020-08-10 12:46:28 PinaColada.local root[1033] INFO Processing page: <PDFPage: Resources={'ProcSet': [/'PDF', /'Text'], 'Font': {'F1': <PDFObjRef:91>, 'F3': <PDFObjRef:86>, 'F4': <PDFObjRef:66>, 'F5': <PDFObjRef:76>, 'F6': <PDFObjRef:71>, 'F12': <PDFObjRef:52>}, 'ExtGState': {'GS1': <PDFObjRef:45>}}, MediaBox=[0, 0, 595.276, 841.89]>
2020-08-10 12:46:28 PinaColada.local root[1033] INFO render_contents: resources={'ProcSet': [/'PDF', /'Text'], 'Font': {'F1': <PDFObjRef:91>, 'F3': <PDFObjRef:86>, 'F4': <PDFObjRef:66>, 'F5': <PDFObjRef:76>, 'F6': <PDFObjRef:71>, 'F12': <PDFObjRef:52>}, 'ExtGState': {'GS1': <PDFObjRef:45>}}, streams=[<PDFStream(27): raw=8536, {'Filter': /'FlateDecode', 'Length': 8535}>], ctm=(1, 0, 0, 1, 0, 0)
2020-08-10 12:46:28 PinaColada.local root[1033] INFO get_font: create

In [53]:
extract_frame = extract_frame.append(pd.DataFrame({'review':to_extract,'extract_doi':references_dict['url']}))

In [56]:
extract_frame

review  \
0    /Users/scotti/surfdrive/Projects/interference_...   
1    /Users/scotti/surfdrive/Projects/interference_...   
2    /Users/scotti/surfdrive/Projects/interference_...   
3    /Users/scotti/surfdrive/Projects/interference_...   
4    /Users/scotti/surfdrive/Projects/interference_...   
5    /Users/scotti/surfdrive/Projects/interference_...   
6    /Users/scotti/surfdrive/Projects/interference_...   
7    /Users/scotti/surfdrive/Projects/interference_...   
8    /Users/scotti/surfdrive/Projects/interference_...   
0    /Users/scotti/surfdrive/Projects/interference_...   
1    /Users/scotti/surfdrive/Projects/interference_...   
2    /Users/scotti/surfdrive/Projects/interference_...   
3    /Users/scotti/surfdrive/Projects/interference_...   
4    /Users/scotti/surfdrive/Projects/interference_...   
5    /Users/scotti/surfdrive/Projects/interference_...   
0    /Users/scotti/surfdrive/Projects/interference_...   
1    /Users/scotti/surfdrive/Projects/interference_...   
2    /Users/scotti/surfdrive/Projects/interference_...   
3    /Users/scotti/surfdrive/Projects/interference_...   
4    /Users/scotti/surfdrive/Projects/interference_...   
5    /Users/scotti/surfdrive/Projects/interference_...   
0    /Users/scotti/surfdrive/Projects/interference_...   
1    /Users/scotti/surfdrive/Projects/interference_...   
2    /Users/scotti/surfdrive/Projects/interference_...   
3    /Users/scotti/surfdrive/Projects/interference_...   
4    /Users/scotti/surfdrive/Projects/interference_...   
5    /Users/scotti/surfdrive/Projects/interference_...   
6    /Users/scotti/surfdrive/Projects/interference_...   
7    /Users/scotti/surfdrive/Projects/interference_...   
8    /Users/scotti/surfdrive/Projects/interference_...   
9    /Users/scotti/surfdrive/Projects/interference_...   
10   /Users/scotti/surfdrive/Projects/interference_...   
11   /Users/scotti/surfdrive/Projects/interference_...   
12   /Users/scotti/surfdrive/Projects/interference_...   
13   /Users/scotti/surfdrive/Projects/interference_...   
14   /Users/scotti/surfdrive/Projects/interference_...   
15   /Users/scotti/surfdrive/Projects/interference_...   
0    /Users/scotti/surfdrive/Projects/interference_...   
1    /Users/scotti/surfdrive/Projects/interference_...   
2    /Users/scotti/surfdrive/Projects/interference_...   
3    /Users/scotti/surfdrive/Projects/interference_...   
4    /Users/scotti/surfdrive/Projects/interference_...   
5    /Users/scotti/surfdrive/Projects/interference_...   
6    /Users/scotti/surfdrive/Projects/interference_...   
7    /Users/scotti/surfdrive/Projects/interference_...   
8    /Users/scotti/surfdrive/Projects/interference_...   
9    /Users/scotti/surfdrive/Projects/interference_...   
10   /Users/scotti/surfdrive/Projects/interference_...   
11   /Users/scotti/surfdrive/Projects/interference_...   
12   /Users/scotti/surfdrive/Projects/interference_...   
13   /Users/scotti/surfdrive/Projects/interference_...   
14   /Users/scotti/surfdrive/Projects/interference_...   
15   /Users/scotti/surfdrive/Projects/interference_...   
16   /Users/scotti/surfdrive/Projects/interference_...   
17   /Users/scotti/surfdrive/Projects/interference_...   
18   /Users/scotti/surfdrive/Projects/interference_...   
19   /Users/scotti/surfdrive/Projects/interference_...   
20   /Users/scotti/surfdrive/Projects/interference_...   
21   /Users/scotti/surfdrive/Projects/interference_...   
22   /Users/scotti/surfdrive/Projects/interference_...   
23   /Users/scotti/surfdrive/Projects/interference_...   
24   /Users/scotti/surfdrive/Projects/interference_...   
25   /Users/scotti/surfdrive/Projects/interference_...   
26   /Users/scotti/surfdrive/Projects/interference_...   
27   /Users/scotti/surfdrive/Projects/interference_...   
28   /Users/scotti/surfdrive/Projects/interference_...   
29   /Users/scotti/surfdrive/Projects/interference_...   
30   /Users/scotti/surfdrive/Projects/interference_...   
31   /Users/scotti/surfdrive/Projects/interfer

In [59]:
len(extract_frame)

3921

In [160]:
references

[{'raw_ref': ['Aron, A.R., 2007. The neural basis of inhibition in cognitive control. Neuroscientist 13 (3), 214–228.'],
  'author': ['Aron, A.R.'],
  'misc': ['The neural basis of inhibition in cognitive control. Neuroscientist 13 (3), 214-228'],
  'year': ['2007']},
 {'raw_ref': ['Aron, A.R., Poldrack, R.A., 2006. Cortical and subcortical contributions to stop signal response inhibition: role of the subthalamic nucleus. J. Neurosci. 26 (9), 2424–2433.'],
  'author': ['Aron, A.R., Poldrack, R.A.'],
  'misc': ['Cortical and subcortical contributions to stop signal response inhibition: role of the subthalamic nucleus'],
  'journal_title': ['J. Neurosci.'],
  'journal_volume': ['26'],
  'journal_page': ['2424-2433'],
  'journal_reference': ['J. Neurosci. 26 () 2424-2433'],
  'year': ['2006']},
 {'raw_ref': ['Aron, A.R., Fletcher, P.C., Bullmore, E.T., Sahakian, B.J., Robbins, T.W., 2003. Stop-signal inhibition disrupted by damage to right inferior frontal gyrus in humans. Nat.'],
  'auth

In [143]:
references_dict

{'url': ['http://dx.doi.org/10.1016/j.biopsych.2016.10.006',
  'http://www.sdmproject.com',
  'ac.uk',
  'http://www.elsevier.com/locate/journal',
  'www.elsevier.com/locate/journal',
  'Reference:']}

In [141]:
extract_from[0]

'/Users/scotti/surfdrive/Projects/interference_in_the_subcortex/save_pdfs/reviews/Functional MRI on executive functioning in aging and dementia  A scoping review of cognitive tasks.pdf'

In [96]:
# Then print the length to make sure number was halved:
print(f'rater 1 has {len(glob.glob("/Users/scotti/surfdrive/Projects/interference_in_the_subcortex/save_pdfs/revs_mck/*"))} reviews to check')
print(f'rater 2 has {len(glob.glob("/Users/scotti/surfdrive/Projects/interference_in_the_subcortex/save_pdfs/revs_sct/*"))} reviews to check')

rater 1 has 28 reviews to check
rater 2 has 28 reviews to check


In [96]:
# What folder to save in?
extra_papers_dir = '/Users/scotti/surfdrive/Projects/interference_in_the_subcortex/save_pdfs/new_from_reviews'

# loop over DOIs from dataframe
for ref in references_dict['url']: 
    # save pdfs
    SciHub(ref, extra_papers_dir).download(choose_scihub_url_index=3)

[INFO] Choose the available link 3: https://sci-hub.se
[INFO] PDF url -> 
	http://dacemirror.sci-hub.se/journal-article/da786a940df9a57e923c8ebf863510cc/diedrichsen2009.pdf
[INFO] Article title -> 
	A probabilistic MR atlas of the human cerebellum
[INFO] Verifying...
[INFO] Verification success.
[100%] Progress: 491138 / 491138
[INFO] Done.                                             
[INFO] Choose the available link 3: https://sci-hub.se
[INFO] PDF url -> 
	http://moscow.sci-hub.se/1926/07d399a1608093373c7f1c65bd1fe06b/tzourio-mazoyer2002.pdf
[INFO] Article title -> 
	Automated Anatomical Labeling of Activations in SPM Using a Macroscopic Anatomical Parcellation of the MNI MRI Single-Subject Brain
[INFO] Verifying...
[INFO] Verification success.
[100%] Progress: 1310152 / 1310152
[INFO] Done.                                             
[INFO] Choose the available link 3: https://sci-hub.se
[INFO] PDF url -> 
	http://twin.sci-hub.se/6141/d2f38c6722d9b1f2b9c49ba129245bd8/buckner2013.pd

AttributeError: 'NoneType' object has no attribute 'attrs'

In [90]:
for ref in references_dict:
    #pdf_n = pdfx.PDFx(ref)
    #pdf_n.download_pdfs("/Users/scotti/surfdrive/Projects/interference_in_the_subcortex/save_pdfs/new_from_reviews")
    #ref.download_pdfs('/Users/scotti/surfdrive/Projects/interference_in_the_subcortex/save_pdfs/new_from_reviews')
    print(ref)

url


In [95]:
references_dict['url'][0]

'https://doi.org/10.1016/j.neuroimage.2009.01.045'

In [47]:
all_reviews[0]

'/Users/scotti/surfdrive/Projects/interference_in_the_subcortex/save_pdfs/reviews/Functional MRI on executive functioning in aging and dementia  A scoping review of cognitive tasks.pdf'

## 2nd: Now download full texts from updated full_text list

In [17]:
# First convert all pmids to DOIs so we can download PDFs easily
import metapub

# create empty dataframe to append to
DOIframe = pd.DataFrame({'pmids': full_texts.index, 'DOIs':'-'})

# loop over pmids to convert to DOIs
for pmid in DOIframe.pmids:
    try:
        DOIframe.loc[DOIframe.pmids==pmid,'DOIs'] = metapub.convert.pmid2doi(pmid)
    except:
        print(DOIframe.loc[DOIframe.pmids==pmid])
        continue

2020-07-23 12:36:38 PinaColada.local metapub.config[76748] WARNING NCBI_API_KEY was not set.


       pmids DOIs
30  24968573    -
        pmids DOIs
152  30125245    -
        pmids DOIs
219  22147454    -
        pmids DOIs
480  21720977    -


In [19]:
# Check which DOIs could not be identifed and manually download their papers
manual_download = DOIframe.loc[DOIframe.DOIs=='-'].pmids
manual_download

30     24968573
152    30125245
219    22147454
480    21720977
Name: pmids, dtype: object

In [ ]:
# Re convert DOIs back to pmids to check that they are correct
for DOI in DOIframe.DOIs:
    try:
        if metapub.convert.doi2pmid(DOI) != DOIframe.loc[DOIframe.DOIs==DOI,'pmids']:
            print('success: ' + str(DOIframe.loc[DOIframe.DOIs==DOI]))
        else:
            print('Incorrect: ' + str(DOIframe.loc[DOIframe.DOIs==DOI]))
    except:
        print("Error cannot find DOI: " + str(DOIframe.loc[DOIframe.pmids==pmid]))
        continue


Error cannot find DOI:         pmids                              DOIs
590  26311607  10.1016/j.neuroimage.2015.08.036
Error cannot find DOI:         pmids                              DOIs
590  26311607  10.1016/j.neuroimage.2015.08.036
Error cannot find DOI:         pmids                              DOIs
590  26311607  10.1016/j.neuroimage.2015.08.036
Error cannot find DOI:         pmids                              DOIs
590  26311607  10.1016/j.neuroimage.2015.08.036
Error cannot find DOI:         pmids                              DOIs
590  26311607  10.1016/j.neuroimage.2015.08.036
Error cannot find DOI:         pmids                              DOIs
590  26311607  10.1016/j.neuroimage.2015.08.036
Error cannot find DOI:         pmids                              DOIs
590  26311607  10.1016/j.neuroimage.2015.08.036
Error cannot find DOI:         pmids                              DOIs
590  26311607  10.1016/j.neuroimage.2015.08.036
Error cannot find DOI:         pmids            

In [20]:
DOIframe.head()

pmids                                    DOIs
0  22056967                10.1136/jnnp-2011-300776
1  25698959                10.3389/fnhum.2015.00034
2  20498351                   10.3758/CABN.10.2.279
3  21232548  10.1016/j.neuropsychologia.2011.01.001
4  24343891                   10.1093/cercor/bht345

In [ ]:
# Now download full texts via sci hub including other references from the previous reviews
from scidownl.scihub import *

# What folder to save in?
out = '/Users/scotti/surfdrive/Projects/interference_in_the_subcortex/save_pdfs/full_texts' 

# loop over DOIs from dataframe
for doi in DOIframe.DOIs: 
    # save pdfs
    SciHub(doi, out).download(choose_scihub_url_index=3)

[INFO] Choose the available link 3: https://sci-hub.se
[INFO] PDF url -> 
	http://zero.sci-hub.se/3282/9dfd6be3048ed00a0d10105ef280ef70/cieslik2015.pdf
[INFO] Article title -> 
	Three key regions for supervisory attentional control  Evidence from neuroimaging meta-analyses
[INFO] Verifying...
[INFO] Verification success.
[100%] Progress: 2267747 / 2267747
[INFO] Done.                                             
[INFO] Choose the available link 3: https://sci-hub.se
[INFO] PDF url -> 
	http://cyber.sci-hub.se/MTAuMTAxNi9qLnRpY3MuMjAxOC4xMC4wMDc=/schilbach2019.pdf
[INFO] Article title -> 
	schilbach2019
[INFO] Verifying...
[INFO] Verification success.
[100%] Progress: 262032 / 262032
[INFO] Done.                                             
[INFO] Choose the available link 3: https://sci-hub.se
[INFO] PDF url -> 
	http://twin.sci-hub.se/7010/029ee63ca8b01fd5cb25c0ae2826c5b2/mckenna2017.pdf
[INFO] Article title -> 
	Informing the Structure of Executive Function in Children  A Meta-Analys

[INFO] Verification success.
[100%] Progress: 383520 / 383520
[INFO] Done.                                             
[INFO] Choose the available link 3: https://sci-hub.se


[INFO] PDF url -> 
	http://dacemirror.sci-hub.se/journal-article/b63b3881b413989fbc457d9544ad74df/reinert2013.pdf
[INFO] Article title -> 
	The Relationship between Executive Function and Obesity in Children and Adolescents  A Systematic Literature Review
[INFO] Verifying...
[INFO] Verification success.
[100%] Progress: 1300914 / 1300914
[INFO] Done.                                             
[INFO] Choose the available link 3: https://sci-hub.se
[INFO] PDF url -> 
	http://twin.sci-hub.se/5873/6d4bf89c33a2fe29cd204ee1a3b35c01/mcteague2016.pdf
[INFO] Article title -> 
	Transdiagnostic impairment of cognitive control in mental illness
[INFO] Verifying...
[INFO] Verification success.
[100%] Progress: 1076029 / 1076029
[INFO] Done.                                             
[INFO] Choose the available link 3: https://sci-hub.se
[INFO] PDF url -> 
	http://dacemirror.sci-hub.se/journal-article/42889e80d73d5901872c1ee92b257aa4/stoodley2011.pdf
[INFO] Article title -> 
	The Cerebellum and 

[INFO] Verification success.
[ 57%] Progress: 932864 / 1622815[100%] Progress: 1622815 / 1622815
[INFO] Done.                                             
[INFO] Choose the available link 3: https://sci-hub.se
[INFO] PDF url -> 
	http://twin.sci-hub.se/5915/adc36cda0ce94ac7673c8ad81ea78869/lei2015.pdf
[INFO] Article title -> 
	Functional MRI reveals different response inhibition between adults and children with ADHD
[INFO] Verifying...
[INFO] Verification success.
[100%] Progress: 256381 / 256381
[INFO] Done.                                             
[INFO] Choose the available link 3: https://sci-hub.se
[INFO] PDF url -> 
	http://twin.sci-hub.se/6816/4d7d0485bc22fd5c549c5355efb5080f/langner2018.pdf
[INFO] Article title -> 
	Towards a human self-regulation system  Common and distinct neural signatures of emotional and behavioural control
[INFO] Verifying...
[INFO] Verification success.
[100%] Progress: 1194977 / 1194977
[INFO] Done.                                             
[INFO

[INFO] Verification success.
[ 86%] Progress: 978944 / 1135468[100%] Progress: 1135468 / 1135468
[INFO] Done.                                             
[INFO] Choose the available link 3: https://sci-hub.se
[INFO] PDF url -> 
	http://dacemirror.sci-hub.se/journal-article/7f0d354b0b4b6de93fc5f6d140c4cca7/10.1080@09297049.2017.1294665.pdf
[INFO] Article title -> 
	Inhibition difficulties in preterm children  Developmental delay or persistent deficit  Child Neuropsychology, 24(6), 734–762
[INFO] Verifying...
[INFO] Verification success.
[100%] Progress: 2181110 / 2181110
[INFO] Done.                                             
[INFO] Choose the available link 3: https://sci-hub.se
[INFO] PDF url -> 
	http://twin.sci-hub.se/6940/dd016b7addea823a6eaa402df836cef4/hung2018.pdf
[INFO] Article title -> 
	Dissociations of cognitive inhibition, response inhibition, and emotional interference  Voxelwise ALE meta-analyses of fMRI studies
[INFO] Verifying...
[INFO] Verification success.
[100%] P

In [32]:
reviews

title  \
pmid                                                          
25446951  Three key regions for supervisory attentional ...   
30442541  From One to Many: Representing Not Only Action...   
28439231  Informing the Structure of Executive Function ...   
26806776  Neuroscience of inhibition for addiction medic...   
29689282  Impulsive aggression and response inhibition i...   
32216846  Comparative meta-analyses of brain structural ...   
29971940  Clarifying cognitive control and the controlla...   
25818684  Putting the brakes on inhibitory models of fro...   
25355218  Dissociable roles of right inferior frontal co...   
29193146                         Control networks and hubs.   
24359877  Systematic review of ERP and fMRI studies inve...   
28868337  The adolescent brain at risk for substance use...   
22457645    Neuroimaging of child abuse: a critical review.   
24070910  Functional neuroanatomy of response inhibition...   
31443912  Neural Substrates of Inhibitory Control Matura...   
30083997  A domain-general brain network underlying emot...   
31942499  Functional MRI on executive functioning in agi...   
23533726  The relationship between executive function an...   
27552532  Transdiagnostic impairment of cognitive contro...   
21373864  The cerebellum and cognition: evidence from fu...   
23663382  Identifying a consistent pattern of neural fun...   
30595231  Error Processing and Inhibitory Control in Obs...   
29042157         Selective inhibition of distracting input.   
25232313  Frontal dysfunctions of impulse control - a sy...   
29980996  Delay knowledge and trial set count modulate u...   
29199109  A supramodal role of the basal ganglia in memo...   
29859551  Medial Frontal Hyperactivation in the Developi...   
23856628  Inhibition and impulsivity: behavioral and neu...   
28456569  Neural correlates of cognitive control in gamb...   
29636070  Neural correlates of interference resolution i...   
29496613  Neural substrates of the emotion-word and emot...   
27911752  Frontosubthalamic Circuits for Control of Acti...   
27895564  Neural Systems Underlying Emotional and Non-em...   
28320224  Identification of Common Neural Circuit Disrup...   
25938917  Functional MRI reveals different response inhi...   
29730485  Towards a human self-regulation system: Common...   
26802874  The interaction between reinforcement and inhi...   
29223025  The intersection between response inhibition a...   
28522823  The influence of emotional interference on cog...   
27887721  Comparative Multimodal Meta-analysis of Struct...   
25793883  The subcortical cocktail problem; mixed signal...   
23247506  Meta-analysis of functional magnetic resonance...   
23164813  Have we been asking the right questions when a...   
31830505  The Stroop effect: An activation likelihood es...   
20600962  Engagement of large-scale networks is related ...   
28961762  Executive Functions Brain System: An Activatio...   
20561537  Early-life stress is associated with impairmen...   
30935439  Failure of activation of striatum during the p...   
29044552  Dynamics of cognitive control: Theoretical bas...   
32189178  Cerebellar Contributions to Proactive and Reac...   
24440116  Inhibition and the right inferior frontal cort...   
28279131  Inhibition difficulties in preterm children: D...   
29923271  Dissociations of cognitive inhibition, respons...   
28551777  Large-scale functional neural network correlat...   
31681058  The Stroop Effect Occurs at Multiple Points Al...   
20977558  Mapping numerical processing, reading, and exe...   

                                                    authors  \
pmid                                                          
25446951  Cieslik, EC., Mueller, VI., Eickhoff, CR., Lan...   
30442541                                       Schilbach, L   
28439231               McKenna, R., Rushe, T., Woodcock, KA   
26806776  Moeller, SJ., Bederson, L., Alia-Klein, N., Go...   
29689282  Puiu, AA., 